In [ ]:
!git clone https://github.com/Varuns-github/emotion-based-music-generator.git

Cloning into 'emotion-based-music-generator'...
remote: Enumerating objects: 304, done.
remote: Counting objects: 100% (49/49), done.
remote: Compressing objects: 100% (44/44), done.
remote: Total 304 (delta 6), reused 45 (delta 5), pack-reused 255
Receiving objects: 100% (304/304), 183.85 MiB | 17.26 MiB/s, done.
Resolving deltas: 100% (18/18), done.
Checking out files: 100% (234/234), done.


In [ ]:
!ls

emotion-based-music-generator  sample_data


In [ ]:
!mkdir angry

In [ ]:
import os

test = os.listdir("emotion-based-music-generator/MusicDataset/Angry")

for i in test:
  
  oldPath = "emotion-based-music-generator/MusicDataset/Angry/" + i
  newPath = "angry/" + i + ".wav"
  print(oldPath)
  !ffmpeg -i $oldPath -ab 320k -ac 2 -ar 44100 -vn $newPath

emotion-based-music-generator/MusicDataset/Angry/142.mp3
ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --ena

In [ ]:
from scipy.io.wavfile import read, write
import pandas as pd

fullMusic = pd.DataFrame()

angry = os.listdir('angry')

for i in angry:
  path = 'angry/' + i
  rate, music = read(path)
  fullMusic = pd.concat([fullMusic , pd.DataFrame(music[0:50000, :])], axis = 0)

In [ ]:
fullMusic

0     1
0         0     0
1        -1     0
2         0     0
3         0     0
4         0     0
...     ...   ...
49995 -1462  4879
49996 -1838  4028
49997 -2377  4077
49998 -2538  4501
49999 -2787  3477

[1500000 rows x 2 columns]

In [ ]:
import numpy as np

def create_train_dataset(df, look_back, train=True):
    dataX1, dataX2 , dataY1 , dataY2 = [],[],[],[]
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        if train:
            dataY1.append(df.iloc[i + look_back, 0])
            dataY2.append(df.iloc[i + look_back, 1])
    if train:
        return np.array(dataX1), np.array(dataX2), np.array(dataY1), np.array(dataY2)
    else:
        return np.array(dataX1), np.array(dataX2)

In [ ]:
X1, X2, y1, y2 = create_train_dataset(fullMusic, look_back=20, train=True)

In [ ]:
print(X1.shape)
print(X2.shape)
print(y1.shape)
print(y2.shape)

(1499979, 1, 20)
(1499979, 1, 20)
(1499979,)
(1499979,)


In [ ]:
X1 = X1.reshape((-1, 1, 20))
X2 = X2.reshape((-1, 1, 20))

In [ ]:

# function to create train data by shifting the music data
def create_test_data(df, look_back):
    dataX1, dataX2 = [], []
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        
    return np.array(dataX1), np.array(dataX2)

In [ ]:
test1, test2 = create_test_data(fullMusic, 20)

In [ ]:
from keras.layers import Dense, LSTM, LeakyReLU
from keras.models import Sequential, load_model

rnn1 = Sequential()
rnn1.add(LSTM(units=100, activation='linear', input_shape=(None, 20)))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=50, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=25, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=12, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=1, activation='linear'))
rnn1.add(LeakyReLU())

rnn1.compile(optimizer='adam', loss='mean_squared_error')
rnn1.fit(X1, y1, epochs=20, batch_size=100)

Epoch 1/20
15000/15000 [==============================] - 83s 5ms/step - loss: 173229.3594
Epoch 2/20
15000/15000 [==============================] - 79s 5ms/step - loss: 104561.9766
Epoch 3/20
15000/15000 [==============================] - 79s 5ms/step - loss: 94444.1406
Epoch 4/20
15000/15000 [==============================] - 78s 5ms/step - loss: 89374.0078
Epoch 5/20
15000/15000 [==============================] - 79s 5ms/step - loss: 86076.6328
Epoch 6/20
15000/15000 [==============================] - 78s 5ms/step - loss: 83690.0391
Epoch 7/20
15000/15000 [==============================] - 79s 5ms/step - loss: 81935.3906
Epoch 8/20
15000/15000 [==============================] - 78s 5ms/step - loss: 80794.2656
Epoch 9/20
15000/15000 [==============================] - 78s 5ms/step - loss: 79419.7344
Epoch 10/20
15000/15000 [==============================] - 78s 5ms/step - loss: 78072.7969
Epoch 11/20
15000/15000 [==============================] - 77s 5ms/step - loss: 77400.9531
Epoch 

In [ ]:
# LSTM Model for channel 2 of the music data
rnn2 = Sequential()
rnn2.add(LSTM(units=100, activation='linear', input_shape=(None, 20)))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=50, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=25, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=12, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=1, activation='linear'))
rnn2.add(LeakyReLU())

rnn2.compile(optimizer='adam', loss='mean_squared_error')
rnn2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
15000/15000 [==============================] - 82s 5ms/step - loss: 206393.5156
Epoch 2/20
15000/15000 [==============================] - 77s 5ms/step - loss: 131052.2109
Epoch 3/20
15000/15000 [==============================] - 79s 5ms/step - loss: 120735.2578
Epoch 4/20
15000/15000 [==============================] - 78s 5ms/step - loss: 115209.2812
Epoch 5/20
15000/15000 [==============================] - 78s 5ms/step - loss: 110444.5391
Epoch 6/20
15000/15000 [==============================] - 77s 5ms/step - loss: 107741.5781
Epoch 7/20
15000/15000 [==============================] - 78s 5ms/step - loss: 106721.6953
Epoch 8/20
15000/15000 [==============================] - 78s 5ms/step - loss: 103469.9141
Epoch 9/20
15000/15000 [==============================] - 79s 5ms/step - loss: 101342.0703
Epoch 10/20
15000/15000 [==============================] - 77s 5ms/step - loss: 100159.1719
Epoch 11/20
15000/15000 [==============================] - 77s 5ms/step - loss: 98300.757

In [ ]:
rnn1.save("music_model_1.h5")

In [ ]:
rnn2.save("music_model_2.h5")

In [ ]:
pred_rnn1 = rnn1.predict(test1.reshape(-1, 1, 20))
pred_rnn2 = rnn2.predict(test2.reshape(-1, 1, 20))

In [ ]:
write('pred_rnn.wav', rate, pd.concat([pd.DataFrame(pred_rnn1.astype('int16')), pd.DataFrame(pred_rnn2.astype('int16'))], axis=1).values)


In [ ]:
from IPython.display import Audio 

a = Audio("pred_rnn.wav")
a